In [3]:
import pandas as pd
import numpy as np
import gensim.downloader
import re
from gensim.models import word2vec, phrases
from gensim.parsing.preprocessing import remove_stopwords, strip_punctuation, strip_numeric,\
                    strip_non_alphanum, strip_multiple_whitespaces, strip_short
from textblob import TextBlob, Word
import collections
from numpy import dot
from numpy.linalg import norm

In [4]:
recipe_df = pd.read_csv('../../data/kaggle_recipes/RAW_recipes.csv')

In [5]:
recipe_df

name      id  minutes  \
0         arriba   baked winter squash mexican style  137739       55   
1                   a bit different  breakfast pizza   31490       30   
2                          all in the kitchen  chili  112140      130   
3                                 alouette  potatoes   59389       45   
4                 amish  tomato ketchup  for canning   44061      190   
...                                              ...     ...      ...   
231632                                   zydeco soup  486161       60   
231633                              zydeco spice mix  493372        5   
231634                     zydeco ya ya deviled eggs  308080       40   
231635        cookies by design   cookies on a stick  298512       29   
231636  cookies by design   sugar shortbread cookies  298509       20   

        contributor_id   submitted  \
0                47892  2005-09-16   
1                26278  2002-06-17   
2               196586  2005-02-25   
3                68585  2003-04-14   
4                41706  2002-10-25   
...                ...         ...   
231632          227978  2012-08-29   
231633         1500678  2013-01-09   
231634           37779  2008-06-07   
231635          506822  2008-04-15   
231636          506822  2008-04-15   

                                                     tags  \
0       ['60-minutes-or-less', 'time-to-make', 'course...   
1       ['30-minutes-or-less', 'time-to-make', 'course...   
2       ['time-to-make', 'course', 'preparation', 'mai...   
3       ['60-minutes-or-less', 'time-to-make', 'course...   
4       ['weeknight', 'time-to-make', 'course', 'main-...   
...                                                   ...   
231632  ['ham', '60-minutes-or-less', 'time-to-make', ...   
231633  ['15-minutes-or-less', 'time-to-make', 'course...   
231634  ['60-minutes-or-less', 'time-to-make', 'course...   
231635  ['30-minutes-or-less', 'time-to-make', 'course...   
231636  ['30-minutes-or-less', 'time-to-make', 'course...   

                                          nutrition  n_steps  \
0             [51.5, 0.0, 13.0, 0.0, 2.0, 0.0, 4.0]       11   
1         [173.4, 18.0, 0.0, 17.0, 22.0, 35.0, 1.0]        9   
2        [269.8, 22.0, 32.0, 48.0, 39.0, 27.0, 5.0]        6   
3         [368.1, 17.0, 10.0, 2.0, 14.0, 8.0, 20.0]       11   
4         [352.9, 1.0, 337.0, 23.0, 3.0, 0.0, 28.0]        5   
...                                             ...      ...   
231632  [415.2, 26.0, 34.0, 26.0, 44.0, 21.0, 15.0]        7   
231633        [14.8, 0.0, 2.0, 58.0, 1.0, 0.0, 1.0]        1   
231634         [59.2, 6.0, 2.0, 3.0, 6.0, 5.0, 0.0]        7   
231635    [188.0, 11.0, 57.0, 11.0, 7.0, 21.0, 9.0]        9   
231636     [174.9, 14.0, 33.0, 4.0, 4.0, 11.0, 6.0]        5   

                                                    steps  \
0       ['make a choice and proceed with recipe', 'dep...   
1       ['preheat oven to 425 degrees f', 'press dough...   
2       ['brown ground beef in large pot', 'add choppe...   
3       ['place potatoes in a large pot of lightly sal...   
4       ['mix all ingredients& boil for 2 1 / 2 hours ...   
...                                                   ...   
231632  ['heat oil in a 4-quart dutch oven', 'add cele...   
231633        ['mix all ingredients together thoroughly']   
231634  ['in a bowl , combine the mashed yolks and may...   
231635  ['place melted butter in a large mixing bowl a...   
231636  ['whip sugar and shortening in a large bowl , ...   

                                              description  \
0       autumn is my favorite time of year to cook! th...   
1       this recipe calls for the crust to be prebaked...   
2       this modified version of 'mom's' chili was a h...   
3       this is a super easy, great tasting, make ahea...   
4       my dh's amish mother raised him on this recipe...   
...                                                   ...   
231632  this is a delicious soup that i originally f

In [6]:
#Extracting only Calories info from nutrition column
def nutrition_clean(i):
    i=i.strip("[]")
    i=i.split(", ")
    i = i[0]
    return i
    
recipe_df["calories_kcal"] = recipe_df["nutrition"].apply(nutrition_clean).astype("float64")

In [7]:
recipe_df.dtypes

name               object
id                  int64
minutes             int64
contributor_id      int64
submitted          object
tags               object
nutrition          object
n_steps             int64
steps              object
description        object
ingredients        object
n_ingredients       int64
calories_kcal     float64
dtype: object

In [8]:
#ingredients, and tags and steps are in string format, need to convert strings to list
def string_to_list(string):
    st = string.strip("[]").split(", ")
    s = [i.strip("''") for i in st]
    return s

In [9]:
recipe_df["tags_list"] = recipe_df["tags"].apply(string_to_list)

In [10]:
recipe_df.head(2)

name      id  minutes  \
0  arriba   baked winter squash mexican style  137739       55   
1            a bit different  breakfast pizza   31490       30   

   contributor_id   submitted  \
0           47892  2005-09-16   
1           26278  2002-06-17   

                                                tags  \
0  ['60-minutes-or-less', 'time-to-make', 'course...   
1  ['30-minutes-or-less', 'time-to-make', 'course...   

                                   nutrition  n_steps  \
0      [51.5, 0.0, 13.0, 0.0, 2.0, 0.0, 4.0]       11   
1  [173.4, 18.0, 0.0, 17.0, 22.0, 35.0, 1.0]        9   

                                               steps  \
0  ['make a choice and proceed with recipe', 'dep...   
1  ['preheat oven to 425 degrees f', 'press dough...   

                                         description  \
0  autumn is my favorite time of year to cook! th...   
1  this recipe calls for the crust to be prebaked...   

                                         ingredients  n_ingredients  \
0  ['winter squash', 'mexican seasoning', 'mixed ...              7   
1  ['prepared pizza crust', 'sausage patty', 'egg...              6   

   calories_kcal                                          tags_list  
0           51.5  [60-minutes-or-less, time-to-make, course, mai...  
1          173.4  [30-minutes-or-less, time-to-make, course, mai...

In [11]:
tag_list = []
for x in recipe_df["tags_list"]:
    for y in x:
        tag_list.append(y)

In [12]:
tag_list

['60-minutes-or-less',
 'time-to-make',
 'course',
 'main-ingredient',
 'cuisine',
 'preparation',
 'occasion',
 'north-american',
 'side-dishes',
 'vegetables',
 'mexican',
 'easy',
 'fall',
 'holiday-event',
 'vegetarian',
 'winter',
 'dietary',
 'christmas',
 'seasonal',
 'squash',
 '30-minutes-or-less',
 'time-to-make',
 'course',
 'main-ingredient',
 'cuisine',
 'preparation',
 'occasion',
 'north-american',
 'breakfast',
 'main-dish',
 'pork',
 'american',
 'oven',
 'easy',
 'kid-friendly',
 'pizza',
 'dietary',
 'northeastern-united-states',
 'meat',
 'equipment',
 'time-to-make',
 'course',
 'preparation',
 'main-dish',
 'chili',
 'crock-pot-slow-cooker',
 'dietary',
 'equipment',
 '4-hours-or-less',
 '60-minutes-or-less',
 'time-to-make',
 'course',
 'main-ingredient',
 'preparation',
 'occasion',
 'side-dishes',
 'eggs-dairy',
 'potatoes',
 'vegetables',
 'oven',
 'easy',
 'dinner-party',
 'holiday-event',
 'easter',
 'cheese',
 'stove-top',
 'dietary',
 'christmas',
 'new-ye

In [13]:
tag_df = pd.DataFrame(tag_list ,columns = {"tags"})
tag_df["n_tags"] = 1
tag_df.groupby("tags").count().sort_values("n_tags", ascending = False)

n_tags
tags                                       
preparation                          230546
time-to-make                         225326
course                               218148
main-ingredient                      170446
dietary                              165091
...                                     ...
marinara-sauce                            1
middle-eastern-main-dish                  1
breakfast-casseroles                      1
high-in-something-diabetic-friendly       1
dips-summer                               1

[552 rows x 1 columns]

In [14]:
recipe_df["ingredients_list"] = recipe_df["ingredients"].apply(string_to_list)

In [15]:
ingred_list =[]
for x in recipe_df["ingredients_list"]:
    for y in x:
        ingred_list.append(y)

In [16]:
ingred_df = pd.DataFrame(ingred_list, columns=["ingredients"])
ingred_df["n_ingred"] = 1
ingred_order = ingred_df.groupby("ingredients").sum().sort_values("n_ingred", ascending=False)
ingred_order

n_ingred
ingredients                                      
salt                                        85746
butter                                      54975
sugar                                       44535
onion                                       39065
water                                       34914
...                                           ...
fat free reduced-sugar cherry yogurt            1
fat free raspberry pecan salad dressing         1
reduced-fat beef hot dog                        1
reduced-fat beef hot dogs                       1
zwieback toast crumbs                           1

[14906 rows x 1 columns]

In [17]:
ingred_order[ingred_order['n_ingred']>1000]

n_ingred
ingredients               
salt                 85746
butter               54975
sugar                44535
onion                39065
water                34914
...                    ...
salmon fillets        1024
pork chops            1024
red bell peppers      1015
elbow macaroni        1007
spaghetti sauce       1001

[319 rows x 1 columns]

In [18]:
recipe_df["tags_list"] = recipe_df["tags"].apply(string_to_list)

In [19]:
recipe_df.dtypes

name                 object
id                    int64
minutes               int64
contributor_id        int64
submitted            object
tags                 object
nutrition            object
n_steps               int64
steps                object
description          object
ingredients          object
n_ingredients         int64
calories_kcal       float64
tags_list            object
ingredients_list     object
dtype: object

In [20]:
recipe_df.head(1)

name      id  minutes  \
0  arriba   baked winter squash mexican style  137739       55   

   contributor_id   submitted  \
0           47892  2005-09-16   

                                                tags  \
0  ['60-minutes-or-less', 'time-to-make', 'course...   

                               nutrition  n_steps  \
0  [51.5, 0.0, 13.0, 0.0, 2.0, 0.0, 4.0]       11   

                                               steps  \
0  ['make a choice and proceed with recipe', 'dep...   

                                         description  \
0  autumn is my favorite time of year to cook! th...   

                                         ingredients  n_ingredients  \
0  ['winter squash', 'mexican seasoning', 'mixed ...              7   

   calories_kcal                                          tags_list  \
0           51.5  [60-minutes-or-less, time-to-make, course, mai...   

                                    ingredients_list  
0  [winter squash, mexican seasoning, mixed spice...

In [21]:
print(list(gensim.downloader.info()['models'].keys()))

['fasttext-wiki-news-subwords-300', 'conceptnet-numberbatch-17-06-300', 'word2vec-ruscorpora-300', 'word2vec-google-news-300', 'glove-wiki-gigaword-50', 'glove-wiki-gigaword-100', 'glove-wiki-gigaword-200', 'glove-wiki-gigaword-300', 'glove-twitter-25', 'glove-twitter-50', 'glove-twitter-100', 'glove-twitter-200', '__testing_word2vec-matrix-synopsis']


In [65]:
def clean_words(list_o_words):
    
    output_list = []
    for word in list_o_words:

        ing = remove_stopwords(word)
        ing = strip_numeric(ing)
        ing = re.sub(r'\(.*oz.\)|(®)|(.*ed)|(.*ly)|boneless|skinless|chunks|fresh|large|cook drain|green|frozen|ground','',ing).strip()
        ing = strip_short(ing,2)
        ing = strip_multiple_whitespaces(ing)
        ing = strip_punctuation(ing)
        ing = strip_non_alphanum(ing)
        ing = (" ".join(TextBlob(ing).words.singularize()))
        output_list.append(ing)
            
    return output_list

In [69]:
clean_words(['asdf','mixed','eat','CPAS'])

['asdf', '', 'eat', 'CPA']

In [66]:
rdf_test = recipe_df[:10]

In [75]:
recipe_df['ingredients_cleaned'] = recipe_df['ingredients_list'].apply(clean_words)

In [74]:
recipe_df.head()

name      id  minutes  \
0  arriba   baked winter squash mexican style  137739       55   
1            a bit different  breakfast pizza   31490       30   
2                   all in the kitchen  chili  112140      130   
3                          alouette  potatoes   59389       45   
4          amish  tomato ketchup  for canning   44061      190   

   contributor_id   submitted  \
0           47892  2005-09-16   
1           26278  2002-06-17   
2          196586  2005-02-25   
3           68585  2003-04-14   
4           41706  2002-10-25   

                                                tags  \
0  ['60-minutes-or-less', 'time-to-make', 'course...   
1  ['30-minutes-or-less', 'time-to-make', 'course...   
2  ['time-to-make', 'course', 'preparation', 'mai...   
3  ['60-minutes-or-less', 'time-to-make', 'course...   
4  ['weeknight', 'time-to-make', 'course', 'main-...   

                                    nutrition  n_steps  \
0       [51.5, 0.0, 13.0, 0.0, 2.0, 0.0, 4.0]       11   
1   [173.4, 18.0, 0.0, 17.0, 22.0, 35.0, 1.0]        9   
2  [269.8, 22.0, 32.0, 48.0, 39.0, 27.0, 5.0]        6   
3   [368.1, 17.0, 10.0, 2.0, 14.0, 8.0, 20.0]       11   
4   [352.9, 1.0, 337.0, 23.0, 3.0, 0.0, 28.0]        5   

                                               steps  \
0  ['make a choice and proceed with recipe', 'dep...   
1  ['preheat oven to 425 degrees f', 'press dough...   
2  ['brown ground beef in large pot', 'add choppe...   
3  ['place potatoes in a large pot of lightly sal...   
4  ['mix all ingredients& boil for 2 1 / 2 hours ...   

                                         description  \
0  autumn is my favorite time of year to cook! th...   
1  this recipe calls for the crust to be prebaked...   
2  this modified version of 'mom's' chili was a h...   
3  this is a super easy, great tasting, make ahea...   
4  my dh's amish mother raised him on this recipe...   

                                         ingredients  n_ingredients  \
0  ['winter squash', 'mexican seasoning', 'mixed ...              7   
1  ['prepared pizza crust', 'sausage patty', 'egg...              6   
2  ['ground beef', 'yellow onions', 'diced tomato...             13   
3  ['spreadable cheese with garlic and herbs', 'n...             11   
4  ['tomato juice', 'apple cider vinegar', 'sugar...              8   

   calories_kcal                                          tags_list  \
0           51.5  [60-minutes-or-less, time-to-make, course, mai...   
1          173.4  [30-minutes-or-less, time-to-make, course, mai...   
2          269.8  [time-to-make, course, preparation, main-dish,...   
3          368.1  [60-minutes-or-less, time-to-make, course, mai...   
4          352.9  [weeknight, time-to-make, course, main-ingredi...   

                                    ingredients_list  \
0  [winter squash, mexican seasoning, mixed spice...   
1  [prepared pizza crust, sausage patty, eggs, mi...   
2  [ground beef, yellow onions, diced tomatoes, t...   
3  [spreadable cheese with garlic and herbs, new ...   
4  [tomato juice, apple cider vinegar, sugar, sal...   

                                 ingredients_cleaned  
0  [winter squash, mexican seasoning, spice, hone...  
1  [pizza crust, sausage patty, egg, milk, salt p...  
2  [beef, yellow onion, tomato, tomato paste, tom...  
3  [spreadable cheese garlic herb, new potato, sh...  
4  [tomato juice, apple cider vinegar, sugar, sal...

In [98]:
all_ingredients = []

for i in range(len(recipe_df)):   
    
    ingreds = recipe_df["ingredients_cleaned"].iloc[i]
#     print(i)
    
    for word in ingreds:
        print(word)
        all_ingredients.append(word)

winter squash
mexican seasoning
spice
honey
butter
olive oil
salt
pizza crust
sausage patty
egg
milk
salt pepper
cheese
beef
yellow onion
tomato
tomato paste
tomato soup
rotel tomato
kidney bean
water
chili powder
cumin
salt
lettuce
dar cheese
spreadable cheese garlic herb
new potato
shallot
parsley
tarragon
olive oil
wine vinegar
salt
pepper
bell pepper
yellow bell pepper
tomato juice
apple cider vinegar
sugar
salt
pepper
clove oil
cinnamon oil
dry mustard
milk
vanilla ice cream
apple juice concentrate
apple

olife
ripe olife
garlic
peppercorn
orange rind
orange juice
chile
extra virgin olive oil
pork sparerib
soy sauce
garlic
ginger
chili powder
coarse black pepper
salt
cilantro leaf
tomato sauce
brown sugar
yellow onion
white vinegar
honey
a original sauce
liquid smoke
black pepper
cumin
dry mustard
cinnamon stick
orange
juice
mirin
water
chocolate sandwich style cookie
chocolate syrup
vanilla ice cream
banana
strawberry ice cream
cream
sugar
butter
banana
egg
lemon juice
orange rin

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



carrot
celery rib
olive oil
low sodium beef bouillon cube
water
tomato bisque soup
sea salt
pepper
pumpkin pie spice
pepper flake
pale ale
chicken stock
shallot
garlic clove
thyme
bay leaf
old bay seasoning
salt
black pepper
small potato
chorizo sausage
corn cob
littleneck clam
mussel
shrimp
lemon
parsley
ge
seafood sauce
steel cut oat
water
salt
skim milk
vanilla
cinnamon
potato
white onion
beef
salt
butter
egg
milk
flmy
sugar
salt
blueberry
cinnamon
chicken stock
egg
parmigiano reggiano cheese
nutmeg
parsley
salt
black pepper
chicken stock
egg
parsley
parmesan cheese
chicken broth
baby spinach
egg
parmesan cheese
white balsamic vinegar
parsley
black pepper
milk
sugar
milk
vanilla extract
light corn syrup
salt
bittersweet chocolate
cornstarch
water
chicken stock
lemon
zest
lemon
juice
salt
egg
spinach
parmesan cheese
lean beef
onion
egg
dry bread crumb
parsley
parmesan cheese
chicken broth
spinach
carrot
pastina
parsley
egg
chicken broth
egg
parmesan cheese
italian parsley
salt pepper

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



hot salsa
olive oil
flmy tortilla
light margarine
onion
garlic clove
cumin
coriander
all purpose flmy
low fat milk
jalapeno pepper
cayenne pepper
salt
tomato
part skim mozzarella cheese
dar cheese
low fat swiss cheese
chicken breast
penne pastum
parmesan cheese
breadcrumb
cooking spray
onion
jalapeno pepper
great northern bean
pinto bean
ketchup
water
molass
yellow mustard
chili powder
liquid smoke
scallion
cilantro
lime juice
garlic clove
chipotle chile adobo
olive oil
oregano
sugar
salt
shrimp
yellow bell pepper
onion
tomatillo
cherry tomato
cooking spray
shallot
garlic clove
spinach
fetum cheese
parmesan cheese
non fat coffee creamer
cannellini bean
black pepper
lemon juice
flmy tortilla
lemon
grapefruit juice
rice vinegar
dark sesame oil
low sodium soy sauce
sherry wine
black pepper
spinach
grapefruit

lasagna noodle
yellow squash
fat free cottage cheese
spinach
part skim mozzarella cheese
parmesan cheese
egg
basil
garlic clove
salt
marinara sauce
chicken breast
ketchup
brown sugar

In [99]:
all_ingredients

['winter squash',
 'mexican seasoning',
 'spice',
 'honey',
 'butter',
 'olive oil',
 'salt',
 'pizza crust',
 'sausage patty',
 'egg',
 'milk',
 'salt pepper',
 'cheese',
 'beef',
 'yellow onion',
 'tomato',
 'tomato paste',
 'tomato soup',
 'rotel tomato',
 'kidney bean',
 'water',
 'chili powder',
 'cumin',
 'salt',
 'lettuce',
 'dar cheese',
 'spreadable cheese garlic herb',
 'new potato',
 'shallot',
 'parsley',
 'tarragon',
 'olive oil',
 'wine vinegar',
 'salt',
 'pepper',
 'bell pepper',
 'yellow bell pepper',
 'tomato juice',
 'apple cider vinegar',
 'sugar',
 'salt',
 'pepper',
 'clove oil',
 'cinnamon oil',
 'dry mustard',
 'milk',
 'vanilla ice cream',
 'apple juice concentrate',
 'apple',
 '',
 'olife',
 'ripe olife',
 'garlic',
 'peppercorn',
 'orange rind',
 'orange juice',
 'chile',
 'extra virgin olive oil',
 'pork sparerib',
 'soy sauce',
 'garlic',
 'ginger',
 'chili powder',
 'coarse black pepper',
 'salt',
 'cilantro leaf',
 'tomato sauce',
 'brown sugar',
 'yellow

In [102]:
model = word2vec.Word2Vec(all_ingredients, \
            vector_size=300, min_count=4, \
            window=10)

In [105]:
model.wv['egg']

KeyError: "Key 'egg' not present"

In [104]:
similar_words = {search_term: [item[0] for item in model.wv.most_similar([search_term], topn=5)]
                  for search_term in ['egg','mango','bread', 'rice']}


KeyError: "Key 'bread' not present in vocabulary"

In [37]:
def ingredients_vector(list_ingredients):
    final_vector = np.zeros(300)
    
    for ingredient in list_ingredients:
        final_vector += model.wv[ingredient]
    
    return final_vector

In [38]:
ingredients_vector(['egg','spinach','rice','salmon'])

array([-1.58557691,  0.32903363,  1.2746598 , -2.59854281, -0.20474219,
       -0.53766109,  0.69603147,  2.94867989,  2.39350289, -0.96435959,
        2.24153293, -3.80292689, -3.03844911,  0.50076437,  1.07700451,
       -3.62920386,  3.38782098, -1.98821933,  1.72152027,  0.3141703 ,
       -0.66900969,  0.91125616,  1.07873117,  3.26103279,  1.64531203,
       -0.78177364, -1.17886779,  3.29321891,  0.7805444 ,  0.06661704,
       -0.88855216, -3.28055564,  1.25261772,  2.31710458,  0.04412234,
       -1.26113921, -0.20567727, -0.19815654,  1.6920754 , -0.69287665,
       -2.2564201 ,  0.49823144,  0.43612812,  3.53300807, -4.14289376,
       -0.49527866, -1.24112465, -2.49250674, -1.36354236, -0.19902216,
        0.30857554, -1.16895869,  0.56106274, -1.37768516,  2.01421994,
       -0.9026862 , -1.82468063, -0.93057087,  0.76800662, -1.68404046,
       -4.82443719, -0.7159574 ,  0.92881553,  2.22723012, -0.77840732,
        2.33392838,  2.54238835,  0.80308011, -2.70495027,  1.42

In [76]:
recipe_vector_dict = {}

In [77]:
for index, row in recipe_df.iterrows():
    print(row['name'], row['ingredients_cleaned'])
    recipe_vector_dict[row['name']] = ingredients_vector(row['ingredients_cleaned'])

arriba   baked winter squash mexican style ['winter squash', 'mexican seasoning', 'spice', 'honey', 'butter', 'olive oil', 'salt']
a bit different  breakfast pizza ['pizza crust', 'sausage patty', 'egg', 'milk', 'salt pepper', 'cheese']
all in the kitchen  chili ['beef', 'yellow onion', 'tomato', 'tomato paste', 'tomato soup', 'rotel tomato', 'kidney bean', 'water', 'chili powder', 'cumin', 'salt', 'lettuce', 'dar cheese']
alouette  potatoes ['spreadable cheese garlic herb', 'new potato', 'shallot', 'parsley', 'tarragon', 'olive oil', 'wine vinegar', 'salt', 'pepper', 'bell pepper', 'yellow bell pepper']
amish  tomato ketchup  for canning ['tomato juice', 'apple cider vinegar', 'sugar', 'salt', 'pepper', 'clove oil', 'cinnamon oil', 'dry mustard']
apple a day  milk shake ['milk', 'vanilla ice cream', 'apple juice concentrate', 'apple']
aww  marinated olives ['', 'olife', 'ripe olife', 'garlic', 'peppercorn', 'orange rind', 'orange juice', 'chile', 'extra virgin olive oil']
backyard sty

KeyError: "Key 'berry cranberry sauce' not present"

In [ ]:
def np_cos_sim(a,b):
    return dot(a, b)/(norm(a)*norm(b))


In [ ]:
def return_best_recipe(list_ing):
    iv = ingredients_vector(list_ing)
    top_score = -2
    top_recipe = None
    for key, value in recipe_vector_dict:
        if np_cos_sim(iv,value) > top_score:
            top_recipe = key
    return key
            
    